##**10. Transformers 라이브러리 사용하기 2**
1. GPT-2 모델 및 tokenizer 실습.
2. Special token 추가.

### **필요 패키지 import**

In [1]:
!pip install transformers

     |████████████████████████████████| 1.8MB 5.6MB/s 
     |████████████████████████████████| 3.2MB 43.6MB/s 
     |████████████████████████████████| 890kB 44.6MB/s 
  Created wheel for sacremoses: filename=sacremoses-0.0.43-cp36-none-any.whl size=893261 sha256=1c4da0a49d99854d6a81e72d5afb527bda08d269706a7a0f465a0ab9405c6166
  Stored in directory: /root/.cache/pip/wheels/29/3c/fd/7ce5c3f0666dab31a50123635e6fb5e19ceb42ce38d4e58f45
Successfully built sacremoses


In [2]:
from transformers import *
from torch import nn
from tqdm import tqdm

import torch

### **GPT-2 불러오기**

In [3]:
gpt_name = 'gpt2'

In [4]:
config = GPT2Config.from_pretrained(gpt_name)
tokenizer = GPT2Tokenizer.from_pretrained(gpt_name)
model = GPT2Model.from_pretrained(gpt_name)

Some weights of GPT2Model were not initialized from the model checkpoint at gpt2 and are newly initialized: ['h.0.attn.masked_bias', 'h.1.attn.masked_bias', 'h.2.attn.masked_bias', 'h.3.attn.masked_bias', 'h.4.attn.masked_bias', 'h.5.attn.masked_bias', 'h.6.attn.masked_bias', 'h.7.attn.masked_bias', 'h.8.attn.masked_bias', 'h.9.attn.masked_bias', 'h.10.attn.masked_bias', 'h.11.attn.masked_bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [5]:
config # 같은 설정이여도 몰델에 따라 정의된 이름이 달라서 doc을 확인해야함

GPT2Config {
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": 50256,
  "embd_pdrop": 0.1,
  "eos_token_id": 50256,
  "gradient_checkpointing": false,
  "initializer_range": 0.02,
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head": 12,
  "n_inner": null,
  "n_layer": 12,
  "n_positions": 1024,
  "resid_pdrop": 0.1,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_labels": true,
  "summary_type": "cls_index",
  "summary_use_proj": true,
  "task_specific_params": {
    "text-generation": {
      "do_sample": true,
      "max_length": 50
    }
  },
  "transformers_version": "4.3.2",
  "use_cache": true,
  "vocab_size": 50257
}

In [6]:
tokenizer # bos : start token, gpt2: pad 토큰 없음 

PreTrainedTokenizer(name_or_path='gpt2', vocab_size=50257, model_max_len=1024, is_fast=False, padding_side='right', special_tokens={'bos_token': AddedToken("<|endoftext|>", rstrip=False, lstrip=False, single_word=False, normalized=True), 'eos_token': AddedToken("<|endoftext|>", rstrip=False, lstrip=False, single_word=False, normalized=True), 'unk_token': AddedToken("<|endoftext|>", rstrip=False, lstrip=False, single_word=False, normalized=True)})

In [7]:
model

GPT2Model(
  (wte): Embedding(50257, 768)
  (wpe): Embedding(1024, 768)
  (drop): Dropout(p=0.1, inplace=False)
  (h): ModuleList(
    (0): Block(
      (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (attn): Attention(
        (c_attn): Conv1D()
        (c_proj): Conv1D()
        (attn_dropout): Dropout(p=0.1, inplace=False)
        (resid_dropout): Dropout(p=0.1, inplace=False)
      )
      (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (mlp): MLP(
        (c_fc): Conv1D()
        (c_proj): Conv1D()
        (dropout): Dropout(p=0.1, inplace=False)
      )
    )
    (1): Block(
      (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (attn): Attention(
        (c_attn): Conv1D()
        (c_proj): Conv1D()
        (attn_dropout): Dropout(p=0.1, inplace=False)
        (resid_dropout): Dropout(p=0.1, inplace=False)
      )
      (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (mlp): MLP(
        (c_fc): Conv1D

### **Tokenizer 사용**

In [8]:
sentence = "I want to go home."
output = tokenizer(sentence)

In [9]:
output

{'input_ids': [40, 765, 284, 467, 1363, 13], 'attention_mask': [1, 1, 1, 1, 1, 1]}

In [10]:
tokenized = tokenizer.tokenize(sentence) # bert와 달리 gpt2는 단어 앞에 띄어쓰기를 삽입함(이상한 G 모양)

In [11]:
tokenized

['I', 'Ġwant', 'Ġto', 'Ġgo', 'Ġhome', '.']

In [12]:
vocab = tokenizer.get_vocab()

In [13]:
print(vocab)
print(len(vocab))

{'!': 0, '"': 1, '#': 2, '$': 3, '%': 4, '&': 5, "'": 6, '(': 7, ')': 8, '*': 9, '+': 10, ',': 11, '-': 12, '.': 13, '/': 14, '0': 15, '1': 16, '2': 17, '3': 18, '4': 19, '5': 20, '6': 21, '7': 22, '8': 23, '9': 24, ':': 25, ';': 26, '<': 27, '=': 28, '>': 29, '?': 30, '@': 31, 'A': 32, 'B': 33, 'C': 34, 'D': 35, 'E': 36, 'F': 37, 'G': 38, 'H': 39, 'I': 40, 'J': 41, 'K': 42, 'L': 43, 'M': 44, 'N': 45, 'O': 46, 'P': 47, 'Q': 48, 'R': 49, 'S': 50, 'T': 51, 'U': 52, 'V': 53, 'W': 54, 'X': 55, 'Y': 56, 'Z': 57, '[': 58, '\\': 59, ']': 60, '^': 61, '_': 62, '`': 63, 'a': 64, 'b': 65, 'c': 66, 'd': 67, 'e': 68, 'f': 69, 'g': 70, 'h': 71, 'i': 72, 'j': 73, 'k': 74, 'l': 75, 'm': 76, 'n': 77, 'o': 78, 'p': 79, 'q': 80, 'r': 81, 's': 82, 't': 83, 'u': 84, 'v': 85, 'w': 86, 'x': 87, 'y': 88, 'z': 89, '{': 90, '|': 91, '}': 92, '~': 93, '¡': 94, '¢': 95, '£': 96, '¤': 97, '¥': 98, '¦': 99, '§': 100, '¨': 101, '©': 102, 'ª': 103, '«': 104, '¬': 105, '®': 106, '¯': 107, '°': 108, '±': 109, '²': 110

In [14]:
vocab['<|endoftext|>'] # end token 역할?

50256

In [15]:
token_ids = [vocab[token] for token in tokenized]
print(token_ids)

[40, 765, 284, 467, 1363, 13]


In [16]:
token_ids = [tokenizer._convert_token_to_id(token) for token in tokenized]
print(token_ids)

[40, 765, 284, 467, 1363, 13]


In [17]:
token_ids = tokenizer.convert_tokens_to_ids(tokenized)
print(token_ids)

[40, 765, 284, 467, 1363, 13]


In [18]:
token_ids = tokenizer.encode(sentence)
print(token_ids)

[40, 765, 284, 467, 1363, 13]


In [19]:
sentence = tokenizer.convert_tokens_to_string(tokenized)
print(sentence)

I want to go home.


In [20]:
tokens = tokenizer.convert_ids_to_tokens(token_ids)
print(tokens)
sentence = tokenizer.convert_tokens_to_string(tokens)
print(sentence)

['I', 'Ġwant', 'Ġto', 'Ġgo', 'Ġhome', '.']
I want to go home.


### **데이터 전처리**

마찬가지로 sample 데이터를 전처리합니다.

In [21]:
data = [
  "I want to go home.",
  "My dog's name is Max.",
  "Natural Language Processing is my favorite research field.",
  "Welcome. How can I help you?",
  "Shoot for the moon. Even if you miss, you'll land among the stars."
]

In [22]:
max_len = 0
batch = []

for sent in tqdm(data):
  token_ids = tokenizer.encode(sent)
  max_len = max(max_len, len(token_ids))
  batch.append(token_ids)

100%|██████████| 5/5 [00:00<00:00, 1134.52it/s]


In [23]:
pad_id = 0 # 아무 토큰이나 패드토큰으로 쓰면 됨

for i, token_ids in enumerate(tqdm(batch)):
  if len(token_ids) < max_len:
    batch[i] = token_ids + [pad_id] * (max_len-len(token_ids))

100%|██████████| 5/5 [00:00<00:00, 2364.32it/s]


In [24]:
batch = torch.LongTensor(batch)

print(batch)
print(batch.shape)

tensor([[   40,   765,   284,   467,  1363,    13,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0],
        [ 3666,  3290,   338,  1438,   318,  5436,    13,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0],
        [35364, 15417, 28403,   318,   616,  4004,  2267,  2214,    13,     0,
             0,     0,     0,     0,     0,     0,     0,     0],
        [14618,    13,  1374,   460,   314,  1037,   345,    30,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0],
        [ 2484,  1025,   329,   262,  8824,    13,  3412,   611,   345,  2051,
            11,   345,  1183,  1956,  1871,   262,  5788,    13]])
torch.Size([5, 18])


In [25]:
batch_mask = (batch != pad_id).float()

print(batch_mask)
print(batch.shape)

tensor([[1., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [1., 1., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [1., 1., 1., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
        [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.]])
torch.Size([5, 18])


### **GPT-2 사용 및 응용**

In [26]:
outputs = model(input_ids=batch, attention_mask=batch_mask)

In [27]:
outputs

BaseModelOutputWithPastAndCrossAttentions([('last_hidden_state',
                                            tensor([[[-7.9628e-02, -6.5353e-02, -8.4245e-02,  ..., -1.4416e-01,
                                                      -4.5576e-02,  1.4250e-02],
                                                     [-1.1001e-01, -3.9448e-01, -1.2587e-01,  ..., -1.9477e-01,
                                                       4.8127e-01,  2.5514e-01],
                                                     [ 1.6084e-01, -4.4684e-01,  7.7317e-01,  ..., -2.7875e-02,
                                                       2.2769e-01,  2.0464e-01],
                                                     ...,
                                                     [ 3.2792e-01, -4.6002e-01,  7.8596e-02,  ...,  3.0025e-02,
                                                      -5.9638e-02,  2.6628e-01],
                                                     [ 3.2829e-01, -4.6319e-01,  8.9981e-02,  ...,  2.447

In [28]:
# B: batch size, L: max length, d_h: hidden size
last_hidden_states = outputs[0]  # (B, L, d_h)

print(last_hidden_states.shape)

torch.Size([5, 18, 768])


다음과 같이 fully connected layer를 하나 사용하여 다음 단어를 예측할 수 있습니다.

In [29]:
lm_linear = nn.Linear(config.hidden_size, config.vocab_size)

In [30]:
# V: vocab size
lm_output = lm_linear(last_hidden_states)  # (B, L, V)

print(lm_output)
print(lm_output.shape)

tensor([[[ 1.4881e+00,  1.8658e+00, -2.1723e+00,  ..., -7.2230e-01,
           6.0422e-01,  1.9318e-01],
         [ 1.8444e-01,  5.4319e+00, -3.9846e+00,  ..., -2.5802e+00,
           2.6267e+00, -1.1002e+00],
         [ 1.4014e-01,  8.6362e+00, -4.9833e+00,  ..., -4.4085e+00,
           3.4220e+00, -1.8155e+00],
         ...,
         [ 2.7958e+00,  8.4075e+00, -7.9105e+00,  ..., -2.4856e+00,
           3.7477e+00, -2.1170e-01],
         [ 2.7860e+00,  8.4218e+00, -7.9018e+00,  ..., -2.4999e+00,
           3.7472e+00, -2.2019e-01],
         [ 2.7805e+00,  8.4282e+00, -7.8968e+00,  ..., -2.5089e+00,
           3.7481e+00, -2.2745e-01]],

        [[ 1.3934e+00,  1.5323e+00, -1.9449e+00,  ..., -4.5503e-01,
           8.0441e-01,  2.6547e-01],
         [ 2.0456e+00,  5.3977e+00, -4.9232e+00,  ..., -1.5916e+00,
           3.0409e+00, -7.7187e-01],
         [ 4.6234e-01,  6.5324e+00, -3.5576e+00,  ..., -3.0594e+00,
           3.2932e+00, -1.5396e+00],
         ...,
         [ 3.1392e+00,  8

GPT-2 역시 다양한 head와 제공됩니다. (https://huggingface.co/transformers/model_doc/gpt2.html)  
위의 Language Modeling을 동일하게 수행할 수 있는 모델은 다음과 같습니다.

In [31]:
lm_model = GPT2LMHeadModel.from_pretrained(gpt_name)

In [32]:
lm_model

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0): Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
      (1): Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): Laye

GPT2LMHeadModel은 `input_ids`와 `labels`를 함께 줄 경우 자동으로 cross entropy loss까지 계산해줍니다.  
`labels`가 주어지지 않을 경우엔 기존과 동일하게 결과만 주어집니다.

In [33]:
outputs = lm_model(input_ids=batch, attention_mask=batch_mask, labels=batch) # input + label을 넣어주면 loss값도 알려줌

In [34]:
outputs

CausalLMOutputWithCrossAttentions([('loss',
                                    tensor(6.2792, grad_fn=<NllLossBackward>)),
                                   ('logits',
                                    tensor([[[ -39.3084,  -39.0100,  -41.8374,  ...,  -46.9337,  -44.9073,
                                               -39.5149],
                                             [ -68.6073,  -68.2685,  -74.1494,  ...,  -76.0179,  -78.3470,
                                               -72.2143],
                                             [-137.8778, -137.4907, -143.7934,  ..., -147.5330, -148.3120,
                                              -140.3080],
                                             ...,
                                             [-128.7599, -127.7347, -129.9467,  ..., -140.4377, -140.0011,
                                              -125.0607],
                                             [-128.9034, -127.8914, -130.1397,  ..., -140.5851, -140.1500,
             

In [35]:
loss = outputs[0]

print(loss)

tensor(6.2792, grad_fn=<NllLossBackward>)


In [36]:
logits = outputs[1]

print(logits)
print(logits.shape)

tensor([[[ -39.3084,  -39.0100,  -41.8374,  ...,  -46.9337,  -44.9073,
           -39.5149],
         [ -68.6073,  -68.2685,  -74.1494,  ...,  -76.0179,  -78.3470,
           -72.2143],
         [-137.8778, -137.4907, -143.7934,  ..., -147.5330, -148.3120,
          -140.3080],
         ...,
         [-128.7599, -127.7347, -129.9467,  ..., -140.4377, -140.0011,
          -125.0607],
         [-128.9034, -127.8914, -130.1397,  ..., -140.5851, -140.1500,
          -125.2252],
         [-128.9673, -127.9750, -130.2378,  ..., -140.6508, -140.2140,
          -125.3020]],

        [[ -33.0736,  -32.3349,  -35.2380,  ...,  -38.3577,  -38.4758,
           -33.0943],
         [ -87.4948,  -88.3811,  -93.4154,  ..., -100.0857,  -94.3312,
           -91.2660],
         [ -97.6050,  -96.2417, -103.4760,  ..., -104.4070, -100.6750,
           -99.1862],
         ...,
         [-136.1583, -134.5683, -137.4096,  ..., -148.0092, -147.4292,
          -131.5333],
         [-136.2986, -134.6973, -137.546

### **Special token 추가하기**

경우에 따라선 별도의 special token을 추가하고 싶을 수 있습니다.  

In [37]:
print(vocab)
print(len(vocab))

{'!': 0, '"': 1, '#': 2, '$': 3, '%': 4, '&': 5, "'": 6, '(': 7, ')': 8, '*': 9, '+': 10, ',': 11, '-': 12, '.': 13, '/': 14, '0': 15, '1': 16, '2': 17, '3': 18, '4': 19, '5': 20, '6': 21, '7': 22, '8': 23, '9': 24, ':': 25, ';': 26, '<': 27, '=': 28, '>': 29, '?': 30, '@': 31, 'A': 32, 'B': 33, 'C': 34, 'D': 35, 'E': 36, 'F': 37, 'G': 38, 'H': 39, 'I': 40, 'J': 41, 'K': 42, 'L': 43, 'M': 44, 'N': 45, 'O': 46, 'P': 47, 'Q': 48, 'R': 49, 'S': 50, 'T': 51, 'U': 52, 'V': 53, 'W': 54, 'X': 55, 'Y': 56, 'Z': 57, '[': 58, '\\': 59, ']': 60, '^': 61, '_': 62, '`': 63, 'a': 64, 'b': 65, 'c': 66, 'd': 67, 'e': 68, 'f': 69, 'g': 70, 'h': 71, 'i': 72, 'j': 73, 'k': 74, 'l': 75, 'm': 76, 'n': 77, 'o': 78, 'p': 79, 'q': 80, 'r': 81, 's': 82, 't': 83, 'u': 84, 'v': 85, 'w': 86, 'x': 87, 'y': 88, 'z': 89, '{': 90, '|': 91, '}': 92, '~': 93, '¡': 94, '¢': 95, '£': 96, '¤': 97, '¥': 98, '¦': 99, '§': 100, '¨': 101, '©': 102, 'ª': 103, '«': 104, '¬': 105, '®': 106, '¯': 107, '°': 108, '±': 109, '²': 110

In [38]:
special_tokens = {
    'bos_token': '[BOS]',
    'eos_token': '[EOS]',
    'pad_token': '[PAD]',
    'additional_special_tokens': ['[SP1]', '[SP2]']
}

In [39]:
num_new_tokens = tokenizer.add_special_tokens(special_tokens) # 토큰 등록
print(num_new_tokens)

5


In [40]:
vocab = tokenizer.get_vocab()
print(vocab)
print(len(vocab))

{'!': 0, '"': 1, '#': 2, '$': 3, '%': 4, '&': 5, "'": 6, '(': 7, ')': 8, '*': 9, '+': 10, ',': 11, '-': 12, '.': 13, '/': 14, '0': 15, '1': 16, '2': 17, '3': 18, '4': 19, '5': 20, '6': 21, '7': 22, '8': 23, '9': 24, ':': 25, ';': 26, '<': 27, '=': 28, '>': 29, '?': 30, '@': 31, 'A': 32, 'B': 33, 'C': 34, 'D': 35, 'E': 36, 'F': 37, 'G': 38, 'H': 39, 'I': 40, 'J': 41, 'K': 42, 'L': 43, 'M': 44, 'N': 45, 'O': 46, 'P': 47, 'Q': 48, 'R': 49, 'S': 50, 'T': 51, 'U': 52, 'V': 53, 'W': 54, 'X': 55, 'Y': 56, 'Z': 57, '[': 58, '\\': 59, ']': 60, '^': 61, '_': 62, '`': 63, 'a': 64, 'b': 65, 'c': 66, 'd': 67, 'e': 68, 'f': 69, 'g': 70, 'h': 71, 'i': 72, 'j': 73, 'k': 74, 'l': 75, 'm': 76, 'n': 77, 'o': 78, 'p': 79, 'q': 80, 'r': 81, 's': 82, 't': 83, 'u': 84, 'v': 85, 'w': 86, 'x': 87, 'y': 88, 'z': 89, '{': 90, '|': 91, '}': 92, '~': 93, '¡': 94, '¢': 95, '£': 96, '¤': 97, '¥': 98, '¦': 99, '§': 100, '¨': 101, '©': 102, 'ª': 103, '«': 104, '¬': 105, '®': 106, '¯': 107, '°': 108, '±': 109, '²': 110

In [41]:
tokenizer

PreTrainedTokenizer(name_or_path='gpt2', vocab_size=50257, model_max_len=1024, is_fast=False, padding_side='right', special_tokens={'bos_token': '[BOS]', 'eos_token': '[EOS]', 'unk_token': AddedToken("<|endoftext|>", rstrip=False, lstrip=False, single_word=False, normalized=True), 'pad_token': '[PAD]', 'additional_special_tokens': ['[SP1]', '[SP2]']})

Special token을 추가했다면 거기에 맞게 모델의 embedding layer의 input size도 바꿔주어야 합니다.

In [42]:
model.resize_token_embeddings(len(vocab))

Embedding(50262, 768)

In [43]:
model

GPT2Model(
  (wte): Embedding(50262, 768)
  (wpe): Embedding(1024, 768)
  (drop): Dropout(p=0.1, inplace=False)
  (h): ModuleList(
    (0): Block(
      (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (attn): Attention(
        (c_attn): Conv1D()
        (c_proj): Conv1D()
        (attn_dropout): Dropout(p=0.1, inplace=False)
        (resid_dropout): Dropout(p=0.1, inplace=False)
      )
      (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (mlp): MLP(
        (c_fc): Conv1D()
        (c_proj): Conv1D()
        (dropout): Dropout(p=0.1, inplace=False)
      )
    )
    (1): Block(
      (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (attn): Attention(
        (c_attn): Conv1D()
        (c_proj): Conv1D()
        (attn_dropout): Dropout(p=0.1, inplace=False)
        (resid_dropout): Dropout(p=0.1, inplace=False)
      )
      (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (mlp): MLP(
        (c_fc): Conv1D